<a href="https://colab.research.google.com/github/StratagemGIS/notebooks/blob/main/data_processing/84_unsafe_roads.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Vaasudevan Srinivasan 🧑🏻‍💻  
StratagemGIS Solutions

In [1]:
%%capture
!pip install mapclassify

In [2]:
import geopandas as gpd
import pooch
from folium import LayerControl

In [3]:
nbrn_file = pooch.retrieve(
    'https://github.com/StratagemGIS/datasets/raw/refs/heads/main/vector/geonb_nbrn-rrnb_shp.zip',
    known_hash='90d36a48b0a53c6320890d1a3bcaee9f9b98d6ad734f910ac6998b01d974b5d5'
)

accidents_file = 'Traffic_Accidents_102100.shp'

In [4]:
accidents = (
    gpd.read_file(accidents_file)
    .query('Year_ != 0')
    .reset_index(drop=True)
    .to_crs('EPSG:2953')
)

nbrn = (
    gpd.read_file(
        nbrn_file,
        layer='geonb_nbrn-rrnb_road-route',
        engine='pyogrio',
    )
    .dropna(subset=['STREETNAME'])
    .query('PLACE_NAME == "Fredericton"')
    .query('STREETNAME != "Unnamed"')
    .dissolve(by='STREETNAME')
    .reset_index()
    .assign(
        STREETNAME=lambda df_: df_.STREETNAME.str.title(),
        road_geom=lambda df_: df_.geometry,
    )
)

In [5]:
result = gpd.GeoDataFrame(
    gpd.sjoin_nearest(accidents, nbrn)
    .groupby(['STREETNAME', 'road_geom'], as_index=False)
    .agg({'OBJECTID_1': 'count'})
    .rename(
        columns={
            'OBJECTID_1': 'Accidents_Count',
            'road_geom': 'geometry',
        }
    )
    .sort_values('Accidents_Count', ascending=False)
    .reset_index(drop=True)
).set_crs('EPSG:2953')

In [6]:
m = result.explore(
    column='Accidents_Count',
    cmap='RdYlGn_r',
    tiles='CartoDB dark_matter',
    legend_kwds={'colorbar': False},
    name='Road Network',
)

accidents[['Year_', 'geometry']].explore(
    m=m,
    column='Year_',
    legend_kwds={'colorbar': False},
    marker_kwds={'radius': 0.01},
    name='Accident Locations',
)

LayerControl().add_to(m)

m

In [7]:
m.save('84_unsafe_roads.html')

In [8]:
result[['STREETNAME', 'Accidents_Count']].head()

STREETNAME  Accidents_Count
0    Regent Street              916
1  Prospect Street              719
2    Smythe Street              349
3     Hanwell Road              320
4      Main Street              305

In [9]:
accidents.Year_.value_counts().sort_index()

Year_
2007    893
2008    967
2009    971
2010    776
2011    869
2012    806
2013    850
2014    815
2015    878
2016    897
2017    578
Name: count, dtype: int64